In [ ]:
!git clone https://github.com/tarun-bisht/lcnn.git > /dev/null
import sys
sys.path.insert(0, 'lcnn/')

Cloning into 'lcnn'...
remote: Enumerating objects: 97, done.
remote: Counting objects: 100% (97/97), done.
remote: Compressing objects: 100% (68/68), done.
remote: Total 97 (delta 44), reused 69 (delta 22), pack-reused 0
Unpacking objects: 100% (97/97), 43.42 KiB | 1.40 MiB/s, done.


In [ ]:
import torch
import torch.nn as nn
import torch.optim as opt
import torch.nn.functional as F
import torchvision.transforms as ttf
import torchvision.datasets as tds
from tqdm.auto import tqdm
import os
import gc
from functools import partial

In [ ]:
from lcnn.models.conv_spectral_norm import convspectralnorm_wrapper
from lcnn.regularized_loss import CELoss
from lcnn.models.layers import ConvBNBlock

In [ ]:
random_seed = 1
torch.backends.cudnn.enabled = False
torch.manual_seed(random_seed)
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(device)

cuda


In [ ]:
def mnist_dataset(batch_size, dataset_path="./temp", val=False):
    labelmap = {idx: idx for idx in range(10)}
    train_dataset = tds.MNIST(root=dataset_path, train=True, download=True, transform=ttf.Compose([ttf.ToTensor()]))
    train_dataloader = torch.utils.data.DataLoader(train_dataset, batch_size=batch_size, shuffle=True)
    if val:
        val_dataset = tds.MNIST(root=dataset_path, train=False, download=True, transform=ttf.Compose([ttf.ToTensor()]))
        val_dataloader = torch.utils.data.DataLoader(val_dataset, batch_size=batch_size, shuffle=True)
        return train_dataloader, val_dataloader, labelmap
    return train_dataloader, labelmap

In [ ]:
class Net(nn.Module):
    def __init__(self, activation):
        super(Net, self).__init__()
        self.conv1 = ConvBNBlock(1, 10, kernel_size=5, bias=False, init_lipschitz=10)
        self.conv2 = ConvBNBlock(10, 20, kernel_size=5, bias=False, init_lipschitz=10)
        self.conv2_drop = nn.Dropout2d()
        self.fc1 = nn.Linear(320, 50)
        self.act1 = activation()
        self.act2 = activation()
        self.fc2 = nn.Linear(50, 10)

    def forward(self, x):
        x = F.max_pool2d(self.conv1(x), 2)
        x = self.act1(x)
        x = F.max_pool2d(self.conv2_drop(self.conv2(x)), 2)
        x = self.act2(x)
        x = x.view(-1, 320)
        x = F.relu(self.fc1(x))
        x = F.dropout(x, training=self.training)
        x = self.fc2(x)
        return x

In [ ]:
def train(network, train_loader, criterion, optimizer, val_loader, model_save_path, device):
    network.train()
    best_val_loss = torch.inf
    train_loss = 0
    for data, target in tqdm(train_loader):
        data, target = data.to(device).requires_grad_(), target.to(device)
        optimizer.zero_grad()
        network.zero_grad()
        loss = criterion.compute_loss(data, target)
        train_loss += criterion.metadata["raw_loss"]
        loss.backward()
        optimizer.step()
    train_loss /= len(train_loader.dataset)
    val_loss, val_acc = test(network, val_loader, device)
    if val_loss < best_val_loss:
        best_val_loss = val_loss
        torch.save(network.state_dict(), os.path.join(model_save_path, "best_model.pt"))
    print("Train Loss", train_loss, "\t", "Val Loss: ", val_loss, "\t", "Val Accuracy: ", val_acc)

In [ ]:
def test(network, test_loader, device):
    network.eval()
    test_loss = 0
    correct = 0
    with torch.no_grad():
        for data, target in tqdm(test_loader):
            data, target = data.to(device), target.to(device)
            output = network(data)
            test_loss += F.cross_entropy(output, target).item()
            pred = output.data.max(1, keepdim=True)[1]
            correct += pred.eq(target.data.view_as(pred)).sum()
        test_loss /= len(test_loader.dataset)
        test_acc = correct / len(test_loader.dataset)
        print("Test Loss: ", test_loss, "\t", "Test Accuracy: ", test_acc.item())
        return test_loss, test_acc.item()

In [ ]:
class GradNormRegularizedLoss(CELoss):
    # norm of gradient of out w.r.t. input
    # usually out are logits or log-probabilites
    def __init__(self,
                model: nn.Module,
                reg_constant: float = 1e-3):
        super().__init__(model)
        self.reg_constant = reg_constant

    def compute_loss(self, input, target):
        out = self.model(input)
        raw_loss = self.loss_criterion(out, target)
        grad_x = torch.autograd.grad(raw_loss, input,
                                    only_inputs=True,
                                    create_graph=True)[0]
        gradnorm = 1e5 * grad_x.pow(2).sum() / input.size(0)

        self.metadata = {
            'raw_loss': raw_loss.item(),
            'gradnorm': gradnorm.item()
        }
        return raw_loss + self.reg_constant * gradnorm

In [ ]:
class CurvatureRegularizedLoss(CELoss):
    # curvature regularization by computing the proxy
    def __init__(self,
                model: nn.Module,
                reg_constants: tuple[float, float] = (1e-2, 1e-2)):
        super().__init__(model)
        self.reg_constants = reg_constants

    @torch.no_grad()
    def _apply_hooks_and_init(self, device):
        # add forward hooks
        self.fwd_handles = []
        for m in self.model.modules():
            if isinstance(m, ConvBNBlock):
                handle_f = m.register_forward_hook(self._extract_lipschitz)
                self.fwd_handles.append(handle_f)
            elif isinstance(m, ParametricSoftplus):
                handle_f = m.register_forward_hook(self._extract_curvature)
                self.fwd_handles.append(handle_f)
            elif isinstance(m, ParametricSwish):
                handle_f = m.register_forward_hook(self._extract_curvature)
                self.fwd_handles.append(handle_f)

        self.modules_visited = []
        self.betas = []
        self.gammas = []
        self.index = 0

    @torch.no_grad()
    def _remove_hooks(self):
        for f in self.fwd_handles:
            f.remove()

    def _extract_lipschitz_residual(self, module, input, output):
        temp1, temp2 = 1, 1

        if type(module.f1) == nn.Conv2d:
            temp1 = module.f1.log_lipschitz
            self.modules_visited.append(module.f1)

        if type(module.f2) == nn.Conv2d:
            temp2 = module.f2.log_lipschitz
            self.modules_visited.append(module.f2)

        self.gammas.append(torch.maximum(temp1, temp2))

    def _extract_lipschitz(self, module, input, output):
        if module not in self.modules_visited:
            self.gammas.append(module.log_lipschitz)

    def _extract_curvature(self, module, input, output):
        self.betas.append(module.log_beta.exp())

    def compute_loss(self, input, target):
        self._apply_hooks_and_init(input.device)
        out = self.model(input)
        self._remove_hooks()

        beta_term = 0.
        for b in self.betas:
            beta_term += b

        if len(self.gammas) > 0:
            gamma_term = 0.
            for g in self.gammas:
                gamma_term += g.abs()

        raw_loss = self.loss_criterion(out, target)
        self.metadata = {
            'raw_loss': raw_loss.item(),
            'beta_term': beta_term.item(),
            'gamma_term': gamma_term.item()
        }

        if len(self.gammas) > 0:
            self.metadata.update({'gamma term:': gamma_term.item()})
            return raw_loss + self.reg_constants[0] * beta_term + self.reg_constants[1] * gamma_term
        else:
            return raw_loss + self.reg_constants[0] * beta_term

In [ ]:
class CurvatureAndGradientRegularizedLoss(CELoss):
    # curvature regularization by computing the proxy
    # also include gradient norm regularization

    def __init__(self,
                model: nn.Module,
                reg_constants: tuple[float, float, float] = (1e-2, 1e-2, 1e-2)):
        super().__init__(model)
        self.reg_constants = reg_constants

    @torch.no_grad()
    def _apply_hooks_and_init(self, device):
        # add forward hooks
        self.fwd_handles = []
        for m in self.model.modules():
            if isinstance(m, ConvBNBlock):
                handle_f = m.register_forward_hook(self._extract_lipschitz)
                self.fwd_handles.append(handle_f)
            elif isinstance(m, ParametricSoftplus):
                handle_f = m.register_forward_hook(self._extract_curvature)
                self.fwd_handles.append(handle_f)
            elif isinstance(m, ParametricSwish):
                handle_f = m.register_forward_hook(self._extract_curvature)
                self.fwd_handles.append(handle_f)

        self.modules_visited = []
        self.betas = []
        self.gammas = []
        self.index = 0

    @torch.no_grad()
    def _remove_hooks(self):
        for f in self.fwd_handles:
            f.remove()

    def _extract_lipschitz_residual(self, module, input, output):
        temp1, temp2 = 1, 1

        if type(module.f1) == nn.Conv2d:
            temp1 = module.f1.log_lipschitz
            self.modules_visited.append(module.f1)

        if type(module.f2) == nn.Conv2d:
            temp2 = module.f2.log_lipschitz
            self.modules_visited.append(module.f2)

        self.gammas.append(torch.maximum(temp1, temp2))

    def _extract_lipschitz(self, module, input, output):
        if module not in self.modules_visited:
            self.gammas.append(module.log_lipschitz)

    def _extract_curvature(self, module, input, output):
        self.betas.append(module.log_beta.exp())

    def compute_loss(self, input, target):
        self._apply_hooks_and_init(input.device)
        out = self.model(input)
        self._remove_hooks()

        beta_term = 0.
        for b in self.betas:
            beta_term += b
        if len(self.gammas) > 0:
            gamma_term = 0.
            for g in self.gammas:
                gamma_term += g.abs()

        raw_loss = self.loss_criterion(out, target)
        loss_grad = torch.autograd.grad(outputs=raw_loss,
                                        inputs=input,
                                        create_graph=True)[0]
        gradnorm = 1e5 * loss_grad.pow(2).sum() / input.size(0)

        self.metadata = {
            'raw_loss': raw_loss.item(),
            'beta_term': beta_term.item() if type(beta_term) == torch.Tensor else beta_term,
            'gamma_term': gamma_term.item() if type(gamma_term) == torch.Tensor else gamma_term,
            'gradnorm': gradnorm.item()
        }

        if len(self.gammas) > 0:
            return raw_loss + self.reg_constants[0] * beta_term  \
                            + self.reg_constants[1] * gamma_term \
                            + self.reg_constants[2] * gradnorm
        else:
            return raw_loss + self.reg_constants[0] * beta_term \
                            + self.reg_constants[2] * gradnorm

In [ ]:
def get_criterion(model, name):
    # Various losses as a dictionary
    loss_dict = {
    'gnorm': partial(GradNormRegularizedLoss, reg_constant=1e-3),
    'curvature': partial(CurvatureRegularizedLoss, reg_constants=(1e-2, 1e-2)),
    'curvature_and_gnorm': partial(CurvatureAndGradientRegularizedLoss, reg_constants=(1e-2, 1e-2, 1e-3))
    }

    loss_fun = loss_dict.get(name, CELoss)
    penalty = loss_fun(model)
    return penalty

In [ ]:
def get_optimizer(lcnn, lr, model: torch.nn.Module):
    # Initialize optimizer and scheduler
    if lcnn:
        # Get beta and gamma parameters if working with LCNNs
        swish_paramnames, psoftplus_paramnames, bn_paramnames = [],[], []
        for (name, layer) in model.named_modules():
            if type(layer) == ParametricSoftplus:
                for p in layer.named_parameters():
                    psoftplus_paramnames.append(name + '.' + p[0])
            if type(layer) == ParametricSwish:
                for p in layer.named_parameters():
                    swish_paramnames.append(name + '.' + p[0])
            if type(layer) == ConvBNBlock:
                for p in layer.named_parameters():
                    if 'log_lipschitz' in p[0]:
                        bn_paramnames.append(name + '.' + p[0])

        softplus_params = list(map(lambda x: x[1],
                                   list(filter(lambda kv: kv[0] in psoftplus_paramnames, model.named_parameters()))))
        swish_params = list(map(lambda x: x[1],
                                   list(filter(lambda kv: kv[0] in swish_paramnames, model.named_parameters()))))
        bn_thresh_params = list(map(lambda x: x[1],
                                    list(filter(lambda kv: kv[0] in bn_paramnames, model.named_parameters()))))
        base_params = list(map(lambda x: x[1],
                               list(filter(
                                   lambda kv: (kv[0] not in psoftplus_paramnames)
                                   and (kv[0] not in swish_paramnames)
                                   and (kv[0] not in bn_paramnames),
                                   model.named_parameters()))))
        model_params = [{'params': base_params},
                        {'params': softplus_params, 'weight_decay': 0.},
                        {'params': swish_params, 'weight_decay': 0.},
                        {'params': bn_thresh_params, 'weight_decay': 0.}]
        optimizer = opt.Adam(model_params, lr=lr)

    else:
        optimizer = opt.Adam(network.parameters(), lr=lr)
    return optimizer

In [ ]:
class ParametricSoftplus(torch.nn.Module):
    # Adapted from:
    # https://discuss.pytorch.org/t/learnable-parameter-in-softplus/60371/2
    # https://pytorch.org/docs/stable/_modules/torch/nn/modules/activation.html#PReLU
    def __init__(self,
                 init_beta: float = 5.,
                 threshold: float = 20.0):
        super().__init__()
        assert init_beta > 0.0
        assert threshold >= 0.0

        # parameterize in terms of log in order to keep beta > 0
        self.log_beta = torch.nn.Parameter(torch.tensor(float(init_beta)).log())
        self.threshold = threshold
        self.register_buffer('offset', torch.log(torch.tensor(2.)), persistent=False)
        self.eps = 1e-3

    def forward(self, x: torch.Tensor) -> torch.Tensor:
        # https://pytorch.org/docs/stable/generated/torch.nn.Softplus.html
        beta = self.log_beta.exp()
        beta_x = (beta + self.eps) * x
        y = (torch.nn.functional.softplus(beta_x, beta=1.0, threshold=self.threshold) - self.offset) / (beta + self.eps)
        return y

In [ ]:
class ParametricSwish(torch.nn.Module):
    def __init__(self,
                 init_beta: float = 5):
        super().__init__()
        assert init_beta >= 0.0

        # parameterize in terms of log in order to keep beta > 0
        self.log_beta = torch.nn.Parameter(torch.tensor(float(init_beta)).log())

    def forward(self, x: torch.Tensor) -> torch.Tensor:
        # https://pytorch.org/docs/stable/generated/torch.nn.SiLU.html
        beta = self.log_beta.exp()
        beta_x = beta*x
        y = x*(torch.nn.functional.sigmoid(beta_x))
        return y

In [ ]:
class Swish(torch.nn.Module):
    def __init__(self,
                 beta: float = 1):
        super().__init__()
        assert beta >= 0.0
        self.beta = beta

    def forward(self, x: torch.Tensor) -> torch.Tensor:
        # https://pytorch.org/docs/stable/generated/torch.nn.SiLU.html
        y = x*(torch.nn.functional.sigmoid(self.beta*x))
        return y

In [ ]:
class NetLCNN(nn.Module):
    def __init__(self, activation):
        super(NetLCNN, self).__init__()
        self.conv1 = ConvBNBlock(1, 10, kernel_size=5, bias=False, init_lipschitz=10, clip_bn=True, conv_wrapper=convspectralnorm_wrapper)
        self.conv2 = ConvBNBlock(10, 20, kernel_size=5, bias=False, init_lipschitz=10, clip_bn=True, conv_wrapper=convspectralnorm_wrapper)
        self.conv2_drop = nn.Dropout2d()
        self.fc1 = torch.nn.utils.parametrizations.spectral_norm(nn.Linear(320, 50))
        self.fc2 = torch.nn.utils.parametrizations.spectral_norm(nn.Linear(50, 10))
        self.act1 = activation()
        self.act2 = activation()

    def forward(self, x):
        x = self.act1(F.max_pool2d(self.conv1(x), 2))
        x = self.act2(F.max_pool2d(self.conv2_drop(self.conv2(x)), 2))
        x = x.view(-1, 320)
        x = F.relu(self.fc1(x))
        x = F.dropout(x, training=self.training)
        x = self.fc2(x)
        return x

In [ ]:
def curvature_hessian_estimator(model: torch.nn.Module,
                        image: torch.Tensor,
                        target: torch.Tensor,
                        num_power_iter: int=20) -> tuple[torch.Tensor, torch.Tensor, torch.Tensor]:

    model.eval()
    u = torch.randn_like(image)
    u /= torch.norm(u, p=2, dim=(1, 2, 3), keepdim=True)

    with torch.enable_grad():
        image = image.requires_grad_()
        out = model(image)
        y = F.log_softmax(out, 1)
        output = F.nll_loss(y, target, reduction='none')
        model.zero_grad()
        # Gradients w.r.t. input
        gradients = torch.autograd.grad(outputs=output.sum(),
                                        inputs=image, create_graph=True)[0]
        gnorm = torch.norm(gradients, p=2, dim=(1, 2, 3))
        assert not gradients.isnan().any()

        # Power method to find singular value of Hessian
        for _ in range(num_power_iter):
            grad_vector_prod = (gradients * u.detach_()).sum()
            hessian_vector_prod = torch.autograd.grad(outputs=grad_vector_prod, inputs=image, retain_graph=True)[0]
            assert not hessian_vector_prod.isnan().any()

            hvp_norm = torch.norm(hessian_vector_prod, p=2, dim=(1, 2, 3), keepdim=True)
            u = hessian_vector_prod.div(hvp_norm + 1e-6) #1e-6 for numerical stability

        grad_vector_prod = (gradients * u.detach_()).sum()
        hessian_vector_prod = torch.autograd.grad(outputs=grad_vector_prod, inputs=image)[0]
        hessian_singular_value = (hessian_vector_prod * u.detach_()).sum((1, 2, 3))

    # curvature = hessian_singular_value / (grad_norm + epsilon) by definition
    curvatures = hessian_singular_value.abs().div(gnorm + 1e-6)
    hess = hessian_singular_value.abs()
    grad = gnorm
    return curvatures, hess, grad

In [ ]:
def measure_curvature(model: torch.nn.Module,
                      dataloader: torch.utils.data.DataLoader,
                      data_fraction: float=0.1,
                      batch_size: int=64,
                      num_power_iter: int=20,
                      device: torch.device='cpu') -> tuple[tuple, tuple, tuple]:

    """
    Compute curvature, hessian norm and gradient norm of a subset of the data given by the dataloader.
    These values are computed using the power method, which requires setting the number of power iterations (num_power_iter).
    """

    model.eval()
    datasize = int(data_fraction * len(dataloader.dataset))
    max_batches = int(datasize / batch_size)
    curvature_agg = torch.zeros(size=(datasize,))
    grad_agg = torch.zeros(size=(datasize,))
    hess_agg = torch.zeros(size=(datasize,))

    for idx, (data, target) in enumerate(dataloader):
        data, target = data.to(device).requires_grad_(), target.to(device)
        with torch.no_grad():
            curvatures, hess, grad = curvature_hessian_estimator(model, data, target, num_power_iter=num_power_iter)
        curvature_agg[idx * batch_size:(idx + 1) * batch_size] = curvatures.detach()
        hess_agg[idx * batch_size:(idx + 1) * batch_size] = hess.detach()
        grad_agg[idx * batch_size:(idx + 1) * batch_size] = grad.detach()

        avg_curvature, std_curvature = curvature_agg.mean().item(), curvature_agg.std().item()
        avg_hessian, std_hessian = hess_agg.mean().item(), hess_agg.std().item()
        avg_grad, std_grad = grad_agg.mean().item(), grad_agg.std().item()

        if idx == (max_batches - 1):
            print('Average Curvature: {:.6f} +/- {:.2f} '.format(avg_curvature, std_curvature))
            print('Average Hessian Spectral Norm: {:.6f} +/- {:.2f} '.format(avg_hessian, std_hessian))
            print('Average Gradient Norm: {:.6f} +/- {:.2f}'.format(avg_grad, std_grad))
            return

In [ ]:
def fgsm(model, X, y, epsilon=0.3):
    """ Construct FGSM adversarial examples on the examples X"""
    delta = torch.zeros_like(X, requires_grad=True)
    with torch.enable_grad():
        pred = model(X + delta)
        loss = nn.CrossEntropyLoss()(pred, y) # Calculate loss
    loss.backward() # Calculate gradient of loss with respect to input
    Xadv = X + epsilon * delta.grad.detach().sign()
    # ensuring valid pixel values
    Xadv = Xadv.clamp(0,1)
    return Xadv

In [ ]:
def pgd(model, X, y, epsilon=0.3, step_size=0.01, num_steps=40):
    """ Construct FGSM adversarial examples on the examples X"""
    Xadv = X #+ 0
    for _ in range(num_steps):
        delta = torch.zeros_like(Xadv, requires_grad=True)
        with torch.enable_grad():
            pred = model(Xadv + delta)
            loss = nn.CrossEntropyLoss()(pred, y) # Calculate loss
        loss.backward() # Calculate gradient of loss with respect to input
        Xadv = Xadv + step_size * delta.grad.detach().sign()
        # imperceptibility condition
        Xadv = torch.min(torch.max(Xadv, X - epsilon), X + epsilon)
        # ensuring valid pixel values
        Xadv = Xadv.clamp(0,1)
    return Xadv

In [ ]:
def adversarial_test(source_model, target_model, attack, device, test_loader):
    torch.cuda.empty_cache()
    gc.collect()
    source_model.to(device)
    target_model.to(device)
    source_model.eval()
    target_model.eval()
    test_loss = 0
    correct = 0
    with torch.no_grad():
        for data, target in tqdm(test_loader):
            data, target = data.to(device), target.to(device)
            adv = attack(source_model, data, target)
            output = target_model(adv)
            test_loss += F.cross_entropy(output, target).item()
            pred = output.argmax(dim=1, keepdim=True)
            correct += pred.eq(target.view_as(pred)).sum().item()
    test_loss /= len(test_loader.dataset)
    test_accuracy = correct/len(test_loader.dataset)
    print('\nAdversarial Test set: Average loss: {:.4f}, Accuracy: {}/{} ({:.0f}%)\n'.format(
        test_loss, correct, len(test_loader.dataset),
        100. * correct / len(test_loader.dataset)))
    return test_loss, test_accuracy

In [ ]:
n_epochs = 10
batch_size_train = 2048
learning_rate = 0.01

In [ ]:
train_loader, test_loader, label = mnist_dataset(batch_size=batch_size_train, val=True)
train_cal_curve_data, test_cal_curve_data, label = mnist_dataset(batch_size=64, val=True)

100%|██████████| 9912422/9912422 [00:00<00:00, 327476104.26it/s]

Extracting ./temp/MNIST/raw/train-images-idx3-ubyte.gz to ./temp/MNIST/raw


100%|██████████| 28881/28881 [00:00<00:00, 118760484.14it/s]


Extracting ./temp/MNIST/raw/train-labels-idx1-ubyte.gz to ./temp/MNIST/raw



100%|██████████| 1648877/1648877 [00:00<00:00, 147561052.24it/s]


Extracting ./temp/MNIST/raw/t10k-images-idx3-ubyte.gz to ./temp/MNIST/raw



100%|██████████| 4542/4542 [00:00<00:00, 23147665.57it/s]

Extracting ./temp/MNIST/raw/t10k-labels-idx1-ubyte.gz to ./temp/MNIST/raw



In [ ]:
attacks_pgd = [partial(pgd, epsilon=0.05, num_steps=10),
               partial(pgd, epsilon=0.1, num_steps=10),
               partial(pgd, epsilon=0.15, num_steps=10),
               partial(pgd, epsilon=0.2, num_steps=10)]

In [ ]:
attacks_fgsm = [partial(fgsm, epsilon=0.05),
                partial(fgsm, epsilon=0.1),
                partial(fgsm, epsilon=0.15),
                partial(fgsm, epsilon=0.2)]

In [ ]:
save_path = "saved_models/simple_ce_softplus_1e3"
os.makedirs(save_path, exist_ok=True)
network = Net(partial(nn.Softplus, beta=1e3)).to(device)
criterion = get_criterion(network, "ce")
optimizer = get_optimizer(False, learning_rate, network)
test(network, test_loader, device)
for epoch in range(1, n_epochs + 1):
    print("Epoch: ", epoch)
    train(network, train_loader, criterion, optimizer, test_loader, save_path, device)
test(network, test_loader, device)
print("Curvature using training data")
print("="*100)
measure_curvature(network, train_cal_curve_data,
                  data_fraction=0.1,
                  batch_size=64,
                  num_power_iter=10,
                  device=device)
print("Curvature using test data")
print("="*100)
measure_curvature(network, test_cal_curve_data,
                  data_fraction=0.1,
                  batch_size=64,
                  num_power_iter=10,
                  device=device)
print("Attacking with PGD (Projected Gradient Descent) Attack")
print("="*100)
for attack in attacks_pgd:
    loss, acc = adversarial_test(source_model=network,
                                 target_model=network,
                                 attack=attack,
                                 device=device,
                                 test_loader=test_loader)

print("Attacking with FGSM (Fast gradient sign method) Attack")
print("="*100)
for attack in attacks_fgsm:
    loss, acc = adversarial_test(source_model=network,
                                 target_model=network,
                                 attack=attack,
                                 device=device,
                                 test_loader=test_loader)

  0%|          | 0/5 [00:00<?, ?it/s]

Test Loss:  0.0011539452075958253 	 Test Accuracy:  0.07279999554157257
Epoch:  1


  0%|          | 0/30 [00:00<?, ?it/s]

  0%|          | 0/5 [00:00<?, ?it/s]

Test Loss:  0.00013927167654037475 	 Test Accuracy:  0.9241999983787537
Train Loss 0.0005595928142468135 	 Val Loss:  0.00013927167654037475 	 Val Accuracy:  0.9241999983787537
Epoch:  2


...


Adversarial Test set: Average loss: 0.0004, Accuracy: 7933/10000 (79%)



  0%|          | 0/5 [00:00<?, ?it/s]


Adversarial Test set: Average loss: 0.0007, Accuracy: 5809/10000 (58%)



  0%|          | 0/5 [00:00<?, ?it/s]


Adversarial Test set: Average loss: 0.0013, Accuracy: 3263/10000 (33%)



In [ ]:
save_path = "saved_models/simple_gnorm_softplus_1e3"
os.makedirs(save_path, exist_ok=True)
network = Net(partial(nn.Softplus, beta=1e3)).to(device)
criterion = get_criterion(network, "gnorm")
optimizer = get_optimizer(False, learning_rate, network)
test(network, test_loader, device)
for epoch in range(1, n_epochs + 1):
    print("Epoch: ", epoch)
    train(network, train_loader, criterion, optimizer, test_loader, save_path, device)
test(network, test_loader, device)
print("Curvature using training data")
print("="*100)
measure_curvature(network, train_cal_curve_data,
                  data_fraction=0.1,
                  batch_size=64,
                  num_power_iter=10,
                  device=device)
print("Curvature using test data")
print("="*100)
measure_curvature(network, test_cal_curve_data,
                  data_fraction=0.1,
                  batch_size=64,
                  num_power_iter=10,
                  device=device)
print("Attacking with PGD (Projected Gradient Descent) Attack")
print("="*100)
for attack in attacks_pgd:
    loss, acc = adversarial_test(source_model=network,
                                 target_model=network,
                                 attack=attack,
                                 device=device,
                                 test_loader=test_loader)

print("Attacking with FGSM (Fast gradient sign method) Attack")
print("="*100)
for attack in attacks_fgsm:
    loss, acc = adversarial_test(source_model=network,
                                 target_model=network,
                                 attack=attack,
                                 device=device,
                                 test_loader=test_loader)

  0%|          | 0/5 [00:00<?, ?it/s]

Test Loss:  0.0011526191473007201 	 Test Accuracy:  0.1136000007390976
Epoch:  1


  0%|          | 0/30 [00:00<?, ?it/s]

  0%|          | 0/5 [00:00<?, ?it/s]

Test Loss:  9.992064386606217e-05 	 Test Accuracy:  0.9484999775886536
Train Loss 0.0005015356441338857 	 Val Loss:  9.992064386606217e-05 	 Val Accuracy:  0.9484999775886536
Epoch:  2


...


Adversarial Test set: Average loss: 0.0004, Accuracy: 7869/10000 (79%)



  0%|          | 0/5 [00:00<?, ?it/s]


Adversarial Test set: Average loss: 0.0008, Accuracy: 5561/10000 (56%)



  0%|          | 0/5 [00:00<?, ?it/s]


Adversarial Test set: Average loss: 0.0013, Accuracy: 3182/10000 (32%)



In [ ]:
save_path = "saved_models/simple_ce_softplus_10"
os.makedirs(save_path, exist_ok=True)
network = Net(partial(nn.Softplus, beta=10)).to(device)
criterion = get_criterion(network, "ce")
optimizer = get_optimizer(False, learning_rate, network)
test(network, test_loader, device)
for epoch in range(1, n_epochs + 1):
    print("Epoch: ", epoch)
    train(network, train_loader, criterion, optimizer, test_loader, save_path, device)
test(network, test_loader, device)
print("Curvature using training data")
print("="*100)
measure_curvature(network, train_cal_curve_data,
                  data_fraction=0.1,
                  batch_size=64,
                  num_power_iter=10,
                  device=device)
print("Curvature using test data")
print("="*100)
measure_curvature(network, test_cal_curve_data,
                  data_fraction=0.1,
                  batch_size=64,
                  num_power_iter=10,
                  device=device)
print("Attacking with PGD (Projected Gradient Descent) Attack")
print("="*100)
for attack in attacks_pgd:
    loss, acc = adversarial_test(source_model=network,
                                 target_model=network,
                                 attack=attack,
                                 device=device,
                                 test_loader=test_loader)

print("Attacking with FGSM (Fast gradient sign method) Attack")
print("="*100)
for attack in attacks_fgsm:
    loss, acc = adversarial_test(source_model=network,
                                 target_model=network,
                                 attack=attack,
                                 device=device,
                                 test_loader=test_loader)

  0%|          | 0/5 [00:00<?, ?it/s]

Test Loss:  0.0011550359725952149 	 Test Accuracy:  0.09319999814033508
Epoch:  1


  0%|          | 0/30 [00:00<?, ?it/s]

  0%|          | 0/5 [00:00<?, ?it/s]

Test Loss:  0.00011417375206947327 	 Test Accuracy:  0.9391999840736389
Train Loss 0.0005344907263914744 	 Val Loss:  0.00011417375206947327 	 Val Accuracy:  0.9391999840736389
Epoch:  2


...


Adversarial Test set: Average loss: 0.0004, Accuracy: 7670/10000 (77%)



  0%|          | 0/5 [00:00<?, ?it/s]


Adversarial Test set: Average loss: 0.0009, Accuracy: 5480/10000 (55%)



  0%|          | 0/5 [00:00<?, ?it/s]


Adversarial Test set: Average loss: 0.0014, Accuracy: 3456/10000 (35%)



In [ ]:
save_path = "saved_models/simple_gnorm_softplus_10"
os.makedirs(save_path, exist_ok=True)
network = Net(partial(nn.Softplus, beta=10)).to(device)
criterion = get_criterion(network, "gnorm")
optimizer = get_optimizer(False, learning_rate, network)
test(network, test_loader, device)
for epoch in range(1, n_epochs + 1):
    print("Epoch: ", epoch)
    train(network, train_loader, criterion, optimizer, test_loader, save_path, device)
test(network, test_loader, device)
print("Curvature using training data")
print("="*100)
measure_curvature(network, train_cal_curve_data,
                  data_fraction=0.1,
                  batch_size=64,
                  num_power_iter=10,
                  device=device)
print("Curvature using test data")
print("="*100)
measure_curvature(network, test_cal_curve_data,
                  data_fraction=0.1,
                  batch_size=64,
                  num_power_iter=10,
                  device=device)
print("Attacking with PGD (Projected Gradient Descent) Attack")
print("="*100)
for attack in attacks_pgd:
    loss, acc = adversarial_test(source_model=network,
                                 target_model=network,
                                 attack=attack,
                                 device=device,
                                 test_loader=test_loader)

print("Attacking with FGSM (Fast gradient sign method) Attack")
print("="*100)
for attack in attacks_fgsm:
    loss, acc = adversarial_test(source_model=network,
                                 target_model=network,
                                 attack=attack,
                                 device=device,
                                 test_loader=test_loader)

  0%|          | 0/5 [00:00<?, ?it/s]

Test Loss:  0.001153630042076111 	 Test Accuracy:  0.08429999649524689
Epoch:  1


  0%|          | 0/30 [00:00<?, ?it/s]

  0%|          | 0/5 [00:00<?, ?it/s]

Test Loss:  9.462961852550507e-05 	 Test Accuracy:  0.9460999965667725
Train Loss 0.00042795609881480536 	 Val Loss:  9.462961852550507e-05 	 Val Accuracy:  0.9460999965667725
Epoch:  2


...


Adversarial Test set: Average loss: 0.0005, Accuracy: 7471/10000 (75%)



  0%|          | 0/5 [00:00<?, ?it/s]


Adversarial Test set: Average loss: 0.0010, Accuracy: 4788/10000 (48%)



  0%|          | 0/5 [00:00<?, ?it/s]


Adversarial Test set: Average loss: 0.0016, Accuracy: 2615/10000 (26%)



In [ ]:
save_path = "saved_models/simple_ce_swish_1e3"
os.makedirs(save_path, exist_ok=True)
network = Net(partial(Swish, beta=1e3)).to(device)
criterion = get_criterion(network, "ce")
optimizer = get_optimizer(False, learning_rate, network)
test(network, test_loader, device)
for epoch in range(1, n_epochs + 1):
    print("Epoch: ", epoch)
    train(network, train_loader, criterion, optimizer, test_loader, save_path, device)
test(network, test_loader, device)
print("Curvature using training data")
print("="*100)
measure_curvature(network, train_cal_curve_data,
                  data_fraction=0.1,
                  batch_size=64,
                  num_power_iter=10,
                  device=device)
print("Curvature using test data")
print("="*100)
measure_curvature(network, test_cal_curve_data,
                  data_fraction=0.1,
                  batch_size=64,
                  num_power_iter=10,
                  device=device)
print("Attacking with PGD (Projected Gradient Descent) Attack")
print("="*100)
for attack in attacks_pgd:
    loss, acc = adversarial_test(source_model=network,
                                 target_model=network,
                                 attack=attack,
                                 device=device,
                                 test_loader=test_loader)

print("Attacking with FGSM (Fast gradient sign method) Attack")
print("="*100)
for attack in attacks_fgsm:
    loss, acc = adversarial_test(source_model=network,
                                 target_model=network,
                                 attack=attack,
                                 device=device,
                                 test_loader=test_loader)

  0%|          | 0/5 [00:00<?, ?it/s]

Test Loss:  0.0011545294761657716 	 Test Accuracy:  0.05309999734163284
Epoch:  1


  0%|          | 0/30 [00:00<?, ?it/s]

  0%|          | 0/5 [00:00<?, ?it/s]

Test Loss:  0.00010327642858028411 	 Test Accuracy:  0.9426999688148499
Train Loss 0.0005136224096020063 	 Val Loss:  0.00010327642858028411 	 Val Accuracy:  0.9426999688148499
Epoch:  2


...


Adversarial Test set: Average loss: 0.0004, Accuracy: 7997/10000 (80%)



  0%|          | 0/5 [00:00<?, ?it/s]


Adversarial Test set: Average loss: 0.0008, Accuracy: 5734/10000 (57%)



  0%|          | 0/5 [00:00<?, ?it/s]


Adversarial Test set: Average loss: 0.0013, Accuracy: 3286/10000 (33%)



In [ ]:
save_path = "saved_models/simple_gnorm_swish_1e3"
os.makedirs(save_path, exist_ok=True)
network = Net(partial(Swish, beta=1e3)).to(device)
criterion = get_criterion(network, "gnorm")
optimizer = get_optimizer(False, learning_rate, network)
test(network, test_loader, device)
for epoch in range(1, n_epochs + 1):
    print("Epoch: ", epoch)
    train(network, train_loader, criterion, optimizer, test_loader, save_path, device)
test(network, test_loader, device)
print("Curvature using training data")
print("="*100)
measure_curvature(network, train_cal_curve_data,
                  data_fraction=0.1,
                  batch_size=64,
                  num_power_iter=10,
                  device=device)
print("Curvature using test data")
print("="*100)
measure_curvature(network, test_cal_curve_data,
                  data_fraction=0.1,
                  batch_size=64,
                  num_power_iter=10,
                  device=device)
print("Attacking with PGD (Projected Gradient Descent) Attack")
print("="*100)
for attack in attacks_pgd:
    loss, acc = adversarial_test(source_model=network,
                                 target_model=network,
                                 attack=attack,
                                 device=device,
                                 test_loader=test_loader)

print("Attacking with FGSM (Fast gradient sign method) Attack")
print("="*100)
for attack in attacks_fgsm:
    loss, acc = adversarial_test(source_model=network,
                                 target_model=network,
                                 attack=attack,
                                 device=device,
                                 test_loader=test_loader)

  0%|          | 0/5 [00:00<?, ?it/s]

Test Loss:  0.0011552131175994872 	 Test Accuracy:  0.10279999673366547
Epoch:  1


  0%|          | 0/30 [00:00<?, ?it/s]

  0%|          | 0/5 [00:00<?, ?it/s]

Test Loss:  0.0001334023043513298 	 Test Accuracy:  0.9253999590873718
Train Loss 0.0005817790548006694 	 Val Loss:  0.0001334023043513298 	 Val Accuracy:  0.9253999590873718
Epoch:  2


...


Adversarial Test set: Average loss: 0.0003, Accuracy: 8355/10000 (84%)



  0%|          | 0/5 [00:00<?, ?it/s]


Adversarial Test set: Average loss: 0.0006, Accuracy: 6794/10000 (68%)



  0%|          | 0/5 [00:00<?, ?it/s]


Adversarial Test set: Average loss: 0.0010, Accuracy: 4749/10000 (47%)



In [ ]:
save_path = "saved_models/simple_ce_swish_10"
os.makedirs(save_path, exist_ok=True)
network = Net(partial(Swish, beta=10)).to(device)
criterion = get_criterion(network, "ce")
optimizer = get_optimizer(False, learning_rate, network)
test(network, test_loader, device)
for epoch in range(1, n_epochs + 1):
    print("Epoch: ", epoch)
    train(network, train_loader, criterion, optimizer, test_loader, save_path, device)
test(network, test_loader, device)
print("Curvature using training data")
print("="*100)
measure_curvature(network, train_cal_curve_data,
                  data_fraction=0.1,
                  batch_size=64,
                  num_power_iter=10,
                  device=device)
print("Curvature using test data")
print("="*100)
measure_curvature(network, test_cal_curve_data,
                  data_fraction=0.1,
                  batch_size=64,
                  num_power_iter=10,
                  device=device)
print("Attacking with PGD (Projected Gradient Descent) Attack")
print("="*100)
for attack in attacks_pgd:
    loss, acc = adversarial_test(source_model=network,
                                 target_model=network,
                                 attack=attack,
                                 device=device,
                                 test_loader=test_loader)

print("Attacking with FGSM (Fast gradient sign method) Attack")
print("="*100)
for attack in attacks_fgsm:
    loss, acc = adversarial_test(source_model=network,
                                 target_model=network,
                                 attack=attack,
                                 device=device,
                                 test_loader=test_loader)

  0%|          | 0/5 [00:00<?, ?it/s]

Test Loss:  0.0011547011613845825 	 Test Accuracy:  0.07750000059604645
Epoch:  1


  0%|          | 0/30 [00:00<?, ?it/s]

  0%|          | 0/5 [00:00<?, ?it/s]

Test Loss:  0.00011636756211519241 	 Test Accuracy:  0.9371999502182007
Train Loss 0.0005071580325563749 	 Val Loss:  0.00011636756211519241 	 Val Accuracy:  0.9371999502182007
Epoch:  2


...


Adversarial Test set: Average loss: 0.0004, Accuracy: 7608/10000 (76%)



  0%|          | 0/5 [00:00<?, ?it/s]


Adversarial Test set: Average loss: 0.0009, Accuracy: 4885/10000 (49%)



  0%|          | 0/5 [00:00<?, ?it/s]


Adversarial Test set: Average loss: 0.0015, Accuracy: 2120/10000 (21%)



In [ ]:
save_path = "saved_models/simple_gnorm_swish_10"
os.makedirs(save_path, exist_ok=True)
network = Net(partial(Swish, beta=10)).to(device)
criterion = get_criterion(network, "gnorm")
optimizer = get_optimizer(False, learning_rate, network)
test(network, test_loader, device)
for epoch in range(1, n_epochs + 1):
    print("Epoch: ", epoch)
    train(network, train_loader, criterion, optimizer, test_loader, save_path, device)
test(network, test_loader, device)
print("Curvature using training data")
print("="*100)
measure_curvature(network, train_cal_curve_data,
                  data_fraction=0.1,
                  batch_size=64,
                  num_power_iter=10,
                  device=device)
print("Curvature using test data")
print("="*100)
measure_curvature(network, test_cal_curve_data,
                  data_fraction=0.1,
                  batch_size=64,
                  num_power_iter=10,
                  device=device)
print("Attacking with PGD (Projected Gradient Descent) Attack")
print("="*100)
for attack in attacks_pgd:
    loss, acc = adversarial_test(source_model=network,
                                 target_model=network,
                                 attack=attack,
                                 device=device,
                                 test_loader=test_loader)

print("Attacking with FGSM (Fast gradient sign method) Attack")
print("="*100)
for attack in attacks_fgsm:
    loss, acc = adversarial_test(source_model=network,
                                 target_model=network,
                                 attack=attack,
                                 device=device,
                                 test_loader=test_loader)

  0%|          | 0/5 [00:00<?, ?it/s]

Test Loss:  0.0011513145923614501 	 Test Accuracy:  0.10159999877214432
Epoch:  1


  0%|          | 0/30 [00:00<?, ?it/s]

  0%|          | 0/5 [00:00<?, ?it/s]

Test Loss:  0.00012654258012771607 	 Test Accuracy:  0.9350000023841858
Train Loss 0.0005690091679493586 	 Val Loss:  0.00012654258012771607 	 Val Accuracy:  0.9350000023841858
Epoch:  2


...


Adversarial Test set: Average loss: 0.0004, Accuracy: 7588/10000 (76%)



  0%|          | 0/5 [00:00<?, ?it/s]


Adversarial Test set: Average loss: 0.0009, Accuracy: 4631/10000 (46%)



  0%|          | 0/5 [00:00<?, ?it/s]


Adversarial Test set: Average loss: 0.0015, Accuracy: 2132/10000 (21%)



In [ ]:
save_path = "saved_models/lcnn_curvature_and_gnorm_softplus"
os.makedirs(save_path, exist_ok=True)
network = NetLCNN(ParametricSoftplus).to(device)
criterion = get_criterion(network, "curvature_and_gnorm")
optimizer = get_optimizer(True, learning_rate, network)
test(network, test_loader, device)
for epoch in range(1, n_epochs + 1):
    print("Epoch: ", epoch)
    train(network, train_loader, criterion, optimizer, test_loader, save_path, device)
test(network, test_loader, device)
print("Curvature using training data")
print("="*100)
measure_curvature(network, train_cal_curve_data,
                  data_fraction=0.1,
                  batch_size=64,
                  num_power_iter=10,
                  device=device)
print("Curvature using test data")
print("="*100)
measure_curvature(network, test_cal_curve_data,
                  data_fraction=0.1,
                  batch_size=64,
                  num_power_iter=10,
                  device=device)
print("Attacking with PGD (Projected Gradient Descent) Attack")
print("="*100)
for attack in attacks_pgd:
    loss, acc = adversarial_test(source_model=network,
                                 target_model=network,
                                 attack=attack,
                                 device=device,
                                 test_loader=test_loader)

print("Attacking with FGSM (Fast gradient sign method) Attack")
print("="*100)
for attack in attacks_fgsm:
    loss, acc = adversarial_test(source_model=network,
                                 target_model=network,
                                 attack=attack,
                                 device=device,
                                 test_loader=test_loader)

  0%|          | 0/5 [00:00<?, ?it/s]

Test Loss:  0.0011526978492736816 	 Test Accuracy:  0.09799999743700027
Epoch:  1


  0%|          | 0/30 [00:00<?, ?it/s]

  0%|          | 0/5 [00:00<?, ?it/s]

Test Loss:  0.000888489842414856 	 Test Accuracy:  0.3042999804019928
Train Loss 0.0007045070290565491 	 Val Loss:  0.000888489842414856 	 Val Accuracy:  0.3042999804019928
Epoch:  2


...


Adversarial Test set: Average loss: 0.0004, Accuracy: 7707/10000 (77%)



  0%|          | 0/5 [00:00<?, ?it/s]


Adversarial Test set: Average loss: 0.0006, Accuracy: 5763/10000 (58%)



  0%|          | 0/5 [00:00<?, ?it/s]


Adversarial Test set: Average loss: 0.0009, Accuracy: 3722/10000 (37%)



In [ ]:
save_path = "saved_models/lcnn_curvature_softplus"
os.makedirs(save_path, exist_ok=True)
network = NetLCNN(ParametricSoftplus).to(device)
criterion = get_criterion(network, "curvature")
optimizer = get_optimizer(True, learning_rate, network)
test(network, test_loader, device)
for epoch in range(1, n_epochs + 1):
    print("Epoch: ", epoch)
    train(network, train_loader, criterion, optimizer, test_loader, save_path, device)
test(network, test_loader, device)
print("Curvature using training data")
print("="*100)
measure_curvature(network, train_cal_curve_data,
                  data_fraction=0.1,
                  batch_size=64,
                  num_power_iter=10,
                  device=device)
print("Curvature using test data")
print("="*100)
measure_curvature(network, test_cal_curve_data,
                  data_fraction=0.1,
                  batch_size=64,
                  num_power_iter=10,
                  device=device)
print("Attacking with PGD (Projected Gradient Descent) Attack")
print("="*100)
for attack in attacks_pgd:
    loss, acc = adversarial_test(source_model=network,
                                 target_model=network,
                                 attack=attack,
                                 device=device,
                                 test_loader=test_loader)

print("Attacking with FGSM (Fast gradient sign method) Attack")
print("="*100)
for attack in attacks_fgsm:
    loss, acc = adversarial_test(source_model=network,
                                 target_model=network,
                                 attack=attack,
                                 device=device,
                                 test_loader=test_loader)

  0%|          | 0/5 [00:00<?, ?it/s]

Test Loss:  0.0011540846824645997 	 Test Accuracy:  0.09799999743700027
Epoch:  1


  0%|          | 0/30 [00:00<?, ?it/s]

  0%|          | 0/5 [00:00<?, ?it/s]

Test Loss:  0.0009528741836547851 	 Test Accuracy:  0.3127000033855438
Train Loss 0.000643498557806015 	 Val Loss:  0.0009528741836547851 	 Val Accuracy:  0.3127000033855438
Epoch:  2


...


Adversarial Test set: Average loss: 0.0003, Accuracy: 7944/10000 (79%)



  0%|          | 0/5 [00:00<?, ?it/s]


Adversarial Test set: Average loss: 0.0006, Accuracy: 5946/10000 (59%)



  0%|          | 0/5 [00:00<?, ?it/s]


Adversarial Test set: Average loss: 0.0009, Accuracy: 3849/10000 (38%)



In [ ]:
save_path = "saved_models/lcnn_curvature_and_gnorm_swish"
os.makedirs(save_path, exist_ok=True)
network = NetLCNN(ParametricSwish).to(device)
criterion = get_criterion(network, "curvature_and_gnorm")
optimizer = get_optimizer(True, learning_rate, network)
test(network, test_loader, device)
for epoch in range(1, n_epochs + 1):
    print("Epoch: ", epoch)
    train(network, train_loader, criterion, optimizer, test_loader, save_path, device)
test(network, test_loader, device)
print("Curvature using training data")
print("="*100)
measure_curvature(network, train_cal_curve_data,
                  data_fraction=0.1,
                  batch_size=64,
                  num_power_iter=10,
                  device=device)
print("Curvature using test data")
print("="*100)
measure_curvature(network, test_cal_curve_data,
                  data_fraction=0.1,
                  batch_size=64,
                  num_power_iter=10,
                  device=device)
print("Attacking with PGD (Projected Gradient Descent) Attack")
print("="*100)
for attack in attacks_pgd:
    loss, acc = adversarial_test(source_model=network,
                                 target_model=network,
                                 attack=attack,
                                 device=device,
                                 test_loader=test_loader)

print("Attacking with FGSM (Fast gradient sign method) Attack")
print("="*100)
for attack in attacks_fgsm:
    loss, acc = adversarial_test(source_model=network,
                                 target_model=network,
                                 attack=attack,
                                 device=device,
                                 test_loader=test_loader)

  0%|          | 0/5 [00:00<?, ?it/s]

Test Loss:  0.0011525011539459229 	 Test Accuracy:  0.13729999959468842
Epoch:  1


  0%|          | 0/30 [00:00<?, ?it/s]

  0%|          | 0/5 [00:00<?, ?it/s]

Test Loss:  0.0008063287734985351 	 Test Accuracy:  0.5027999877929688
Train Loss 0.0006797398577133815 	 Val Loss:  0.0008063287734985351 	 Val Accuracy:  0.5027999877929688
Epoch:  2


...


Adversarial Test set: Average loss: 0.0004, Accuracy: 7529/10000 (75%)



  0%|          | 0/5 [00:00<?, ?it/s]


Adversarial Test set: Average loss: 0.0007, Accuracy: 5402/10000 (54%)



  0%|          | 0/5 [00:00<?, ?it/s]


Adversarial Test set: Average loss: 0.0010, Accuracy: 3420/10000 (34%)



In [ ]:
save_path = "saved_models/lcnn_curvature_swish"
os.makedirs(save_path, exist_ok=True)
network = NetLCNN(ParametricSwish).to(device)
criterion = get_criterion(network, "curvature")
optimizer = get_optimizer(True, learning_rate, network)
test(network, test_loader, device)
for epoch in range(1, n_epochs + 1):
    print("Epoch: ", epoch)
    train(network, train_loader, criterion, optimizer, test_loader, save_path, device)
test(network, test_loader, device)
print("Curvature using training data")
print("="*100)
measure_curvature(network, train_cal_curve_data,
                  data_fraction=0.1,
                  batch_size=64,
                  num_power_iter=10,
                  device=device)
print("Curvature using test data")
print("="*100)
measure_curvature(network, test_cal_curve_data,
                  data_fraction=0.1,
                  batch_size=64,
                  num_power_iter=10,
                  device=device)
print("Attacking with PGD (Projected Gradient Descent) Attack")
print("="*100)
for attack in attacks_pgd:
    loss, acc = adversarial_test(source_model=network,
                                 target_model=network,
                                 attack=attack,
                                 device=device,
                                 test_loader=test_loader)

print("Attacking with FGSM (Fast gradient sign method) Attack")
print("="*100)
for attack in attacks_fgsm:
    loss, acc = adversarial_test(source_model=network,
                                 target_model=network,
                                 attack=attack,
                                 device=device,
                                 test_loader=test_loader)

  0%|          | 0/5 [00:00<?, ?it/s]

Test Loss:  0.0011536531925201417 	 Test Accuracy:  0.10369999706745148
Epoch:  1


  0%|          | 0/30 [00:00<?, ?it/s]

  0%|          | 0/5 [00:00<?, ?it/s]

Test Loss:  0.0008750490665435791 	 Test Accuracy:  0.26579999923706055
Train Loss 0.0007879385193188985 	 Val Loss:  0.0008750490665435791 	 Val Accuracy:  0.26579999923706055
Epoch:  2


...


Adversarial Test set: Average loss: 0.0004, Accuracy: 7137/10000 (71%)



  0%|          | 0/5 [00:00<?, ?it/s]


Adversarial Test set: Average loss: 0.0008, Accuracy: 4780/10000 (48%)



  0%|          | 0/5 [00:00<?, ?it/s]


Adversarial Test set: Average loss: 0.0012, Accuracy: 2296/10000 (23%)

